In [2]:
import numpy as np
import os
import pandas as pd
from src.utilities.fin_shape_utils import plot_mesh
from src.utilities.fin_class_def import FinData
from src.utilities.functions import path_leaf
import glob2 as glob
import trimesh
from tqdm import tqdm
import meshplot as mp
import pyvista as pv

In [3]:
# get list of refined fin mesh objects
# root = "/media/nick/hdd02/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/pecfin_dynamics/"
root = "/Users/nick/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/pecfin_dynamics/"
fin_mesh_list = sorted(glob.glob(os.path.join(root, "point_cloud_data", "processed_fin_data", "*smoothed_fin_mesh*")))

# load metadata
fin_stats_df = pd.read_csv(os.path.join(root, "metadata", "fin_stats.csv"))
fin_stats_df["experiment_date"] = fin_stats_df["experiment_date"].astype(str)
fin_stats_df.head()

# set write directory
figure_dir = os.path.join(root, "point_cloud_data", "fin_shape_analyses")
if not os.path.isdir(figure_dir):
    os.makedirs(figure_dir) 

### Make rotating point cloud plots using pyvista rendering

In [4]:
import plotly.colors as pc
import matplotlib.colors as mc

# Get Plotly's default discrete colors (hex format)
plotly_default_colors_hex = pc.qualitative.Plotly

# Convert hex colors to RGB triplets
plotly_rgb = [mc.hex2color(hex_color) for hex_color in plotly_default_colors_hex]

set2_colors = pc.qualitative.Set2

# Convert hex colors to RGB triplets (0-255 range)
set2_rgb = [
    list(map(int, color[color.find("(")+1 : color.find(")")].split(",")))
    for color in set2_colors
]

In [29]:
from plotly.subplots import make_subplots

well_num0 = 53
date_string0 = "20240711_01"
time_num0 = 0

well_num1 = 11
date_string1 = "20240711_02"
time_num1 = 0

date_ft0 = fin_stats_df["experiment_date"] == date_string0
well_ft0 = fin_stats_df["well_index"] == well_num0
time_ft0 = fin_stats_df["time_index"] == time_num0

date_ft1 = fin_stats_df["experiment_date"] == date_string1
well_ft1 = fin_stats_df["well_index"] == well_num1
time_ft1 = fin_stats_df["time_index"] == time_num1

# meta_temp = metadata_df.loc[date_ft0 & well_ft0 & time_ft0, :].reset_index(drop=True)

# load points sets
file_stub0 = f"{date_string0}_well{well_num0:04}_time{time_num0:04}"
fname0 = file_stub0 + "_smoothed_fin_mesh.obj"
fpath0 = os.path.join(root, "point_cloud_data", "processed_fin_data", fname0)
fin_mesh0 = trimesh.load(fpath0)

file_stub1 = f"{date_string1}_well{well_num1:04}_time{time_num1:04}"
fname1 = file_stub1 + "_smoothed_fin_mesh.obj"
fpath1 = os.path.join(root, "point_cloud_data", "processed_fin_data", fname1)
fin_mesh1 = trimesh.load(fpath1)

fig, lines0, mesh0 = plot_mesh(fin_mesh0, surf_alpha=1)
_, lines1, mesh1 = plot_mesh(fin_mesh1, surf_alpha=1)


fig = make_subplots(rows=1, cols=2, specs=[[{'type': 'scene'}, {'type': 'scene'}]], subplot_titles=("Mesh 1", "Mesh 2"))

fig.add_trace(mesh0, row=1, col=1)
fig.add_trace(lines0, row=1, col=1)

fig.add_trace(mesh1, row=1, col=2)
fig.add_trace(lines1, row=1, col=2)
fig.show()

In [21]:
# Set initial camera view
camera = dict(eye=dict(x=1.5, y=1.5, z=1))  # Initial camera position
fig.update_layout(scene_camera=camera)

# Number of rotation steps and output folder
num_frames = 36  # Number of rotation angles (e.g., 36 frames for a full 360° rotation)
output_folder = os.path.join(figure_dir, file_stub + "_rotation_frames")

# Create the output folder if it doesn't exist
os.makedirs(output_folder, exist_ok=True)

# fig.show()
# Rotate the camera and save frames
for i in tqdm(range(num_frames)):
    # Calculate the azimuth angle
    angle = i * (360 / num_frames)

    # Update the camera view by modifying the x and y positions of the eye
    camera['eye'] = dict(
        x=1.5 * round(np.cos(angle * 3.14159 / 180), 3),  # x-position based on angle
        y=1.5 * round(np.sin(angle * 3.14159 / 180), 3),  # y-position based on angle
        z=1  # Keep z constant
    )

    # Apply the updated camera view to the figure
    fig.update_layout(scene_camera=camera)

    # Save the current frame as a PNG file
    frame_path = os.path.join(output_folder, f"frame_{i:03d}.png")
    fig.write_image(frame_path, width=800, height=600)

100%|██████████| 36/36 [00:52<00:00,  1.46s/it]


In [16]:
frame_dir = os.path.join(figure_dir, "point_frames2")
os.makedirs(frame_dir, exist_ok=True)

z_rot = False
data_ind = 43

# get key metadata
date_string = fin_stats_df.loc[data_ind, "experiment_date"]
well_num = fin_stats_df.loc[data_ind, "well_index"]
time_num = fin_stats_df.loc[data_ind, "time_index"]

# other metadata
chem_i = fin_stats_df.loc[data_ind, "chem_i"]
print(chem_i)
# load points sets
file_stub = f"{date_string}_well{well_num:04}_time{time_num:04}"
fname_c = file_stub + "_fin_data_upsampled.csv"
fpath_c = os.path.join(root, "point_cloud_data", "processed_fin_data", fname_c)
fin_df_u = pd.read_csv(fpath_c)
fin_df = fin_df_u.loc[:, ["nucleus_id", "XB", "YB", "ZB"]].groupby("nucleus_id").mean().reset_index()

# make output directory 
frame_sub_dir = os.path.join(frame_dir, file_stub + "_" + chem_i, "")
if not os.path.isdir(frame_sub_dir):
    os.makedirs(frame_sub_dir)
# fin_df.head()


# Create a PyVista plotter
# plotter.close()
plotter = pv.Plotter()

# Add spheres for each point in the point cloud
for i in range(fin_df.shape[0]):
    point = fin_df.loc[i, ["XB", "YB", "ZB"]].to_numpy()
    ci = np.random.choice(np.arange(len(set2_rgb)), 1)[0]
    sphere = pv.Sphere(radius=5, center=point)
    plotter.add_mesh(sphere, color=set2_rgb[ci])

    plotter.add_mesh(
        sphere,
        color=plotly_rgb[ci],
        specular=0.9,           # Control the intensity of the shine
        specular_power=25       # Control the sharpness of the shine
    )

# Show the plotter in a separate window
# plotter.show(auto_close=False)  # Keep the plot window open

# Initial camera position, focus, and up vector
pos = [28.64440092444413, -369.2201064562611, 231.99626877216642]
plotter.camera.position = pos
initial_position = plotter.camera.position  # (camera_x, camera_y, camera_z)
focus = plotter.camera.focal_point  
initial_up = np.array(plotter.camera.up)
initial_view_vector = np.asarray(initial_position) - np.asarray(focus)

# Create a loop to rotate the camera around the focus point
radius = np.linalg.norm(np.array(initial_position) - np.array(focus))
angle_step = np.radians(5)  # Rotation step in radians
angle_vec = np.arange(0, 2*np.pi, angle_step)
for a, angle in enumerate(tqdm(angle_vec)):
    # Update camera position based on rotation
    if z_rot:
        new_position = [
            focus[0] + radius * np.cos(angle),  # X-coordinate
            focus[1] + radius * np.sin(angle),  # Y-coordinate
            initial_position[2]                # Z-coordinate (keep constant for horizontal rotation)
        ]
        plotter.camera.position = new_position
    else:
        # Define rotation matrix around X-axis
        cos_angle = np.cos(angle)
        sin_angle = np.sin(angle)
        rotation_matrix = np.array([
            [1,         0,          0        ],
            [0,  cos_angle, -sin_angle],
            [0,  sin_angle,  cos_angle]
        ])

        # Rotate the view vector
        rotated_view_vector = rotation_matrix @ initial_view_vector
    
        # Rotate the up vector
        rotated_up = rotation_matrix @ initial_up
        
         # Update camera position and up vector
        new_position = focus + rotated_view_vector
        plotter.camera.position = new_position.tolist()
        plotter.camera.up = rotated_up.tolist()
        
    
    # plotter.camera.up = up
    frame_path = os.path.join(frame_sub_dir, f"frame_{a:03d}.png")
    # 
    # Redraw the plot with updated camera
    plotter.render()

    plotter.screenshot(frame_path)

    # # Small delay for smooth animation
    # time.sleep(0.05)
plotter.close()  
# Show the interactive plot
# plotter.show()


DMSO_36


100%|██████████| 72/72 [00:04<00:00, 14.89it/s]


In [9]:
focus

(16.764299392700195, 3.572603225708008, 28.644401520490646)

In [66]:
# sort array and DF for clarity
indices = np.lexsort((dist_df['chem_id'], dist_df['chem_time']))
dist_df_s = dist_df.iloc[indices]

dist_arr0_s = dist_arr0.copy()
dist_arr0_s = dist_arr0_s[indices, :]
dist_arr0_s = dist_arr0_s[:, indices]

dist_arr1_s = dist_arr1.copy()
dist_arr1_s = dist_arr1_s[indices, :]
dist_arr1_s = dist_arr1_s[:, indices]

dist_arr2_s = dist_arr2.copy()
dist_arr2_s = dist_arr2_s[indices, :]
dist_arr2_s = dist_arr2_s[:, indices]

dist_arr3_s = dist_arr3.copy()
dist_arr3_s = dist_arr3_s[indices, :]
dist_arr3_s = dist_arr3_s[:, indices]

In [67]:
# save 
dist_df_s.to_csv(os.path.join(write_dir, "emd_dist_df.csv"), index=False)

np.save(os.path.join(write_dir, "surf_dist_arr.npy"), dist_arr0_s)
np.save(os.path.join(write_dir, "centroid_dist_arr.npy"), dist_arr1_s)
np.save(os.path.join(write_dir, "surf_dist_norm_arr.npy"), dist_arr2_s)
np.save(os.path.join(write_dir, "centroid_dist_norm_arr.npy"), dist_arr3_s)